In [1]:
import tensorflow as tf
from functools import partial

### [Optional.  Tensorflow Graph Visualization ]

---

> _Jupyter에서 Tensorflow에서 구성되는 Graph를 시각적으로 보여주기 위한 helper 메소드입니다._<br>

In [2]:
from IPython.display import clear_output, Image, display, HTML
import numpy as np    

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = "<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))

    display(HTML(iframe))

## Convolutional Layers 구성하기
---

이 모델의 Feature Extractor는 Maxpooling과 Convolution Layer가 교차되는 형식으로 구성되었습니다.<br>
특이 사항으로는 width 방향으로 동적 길이를 가집니다. <br>

코드 작업의 편리함을 위해, 우리는 이미지를 한번 전치 후 사용합니다.

In [3]:
heights = 28
num_classes = 10

graph = tf.Graph()
with graph.as_default():
    x = tf.placeholder(tf.float32, shape=(None,heights,None,1),name='image')
    is_train = tf.placeholder_with_default(False,None,name='is_train')
    
    with tf.variable_scope("conv_layers"):
        conv_layer = partial(tf.layers.Conv2D,
                             kernel_size=(3,3),
                             padding='same',
                             activation=tf.nn.relu)
        maxpool_layer = partial(tf.layers.MaxPooling2D,
                                pool_size=(2,2),
                                strides=(2,2),
                                padding='same')
        BN = tf.layers.BatchNormalization
        
        transposed_x = tf.transpose(x,[0,2,1,3])
        conv1 = conv_layer(64,name='conv1')(transposed_x)
        max1 = maxpool_layer(name='maxpool1')(conv1)
        conv2 = conv_layer(128,name='conv2')(max1)    
        max2 = maxpool_layer(name='maxpool2')(conv2)
        conv3 = conv_layer(256,name='conv3')(max2)
        conv4 = conv_layer(256,name='conv4')(conv3)
        max3 = maxpool_layer(name='maxpool3')(conv4)
        
        conv5 = conv_layer(512,name='conv5')(max3)
        bn1 = BN(name='bn1')(conv5,training=is_train)
        conv6 = conv_layer(512,name='conv6')(bn1)
        bn2 = BN(name='bn2')(conv6,training=is_train)
        max4 = maxpool_layer(pool_size=(1,2),
                             strides=(1,2),
                             name='maxpool4')(bn2)
        
        conv7 = conv_layer(512,kernel_size=(2,2),
                           name='conv7')(max4)

Instructions for updating:
Colocations handled automatically by placer.


In [4]:
show_graph(graph)

## Convolution layer to RNN Layer로 맵핑하는 부분 구성
---

Convolution Layer을 통과하고 나면<br>
Shape : (batch_size, feature_map_width, feature_map_height, num_features)로 구성됩니다.<br>

현재 글자는 X축 방향으로 진행되고 있기 때문에, x축 방향이 time step 방향이 됩니다.<br>
RNN의 Input으로 넣기 위해 <br>
Shape : (batch_size, feature_map_width, feature_map_height * num_features)으로<br>
바꾸어주어야 합니다.

In [5]:
with graph.as_default():
    with tf.variable_scope('map-to-sequence'):
        shape = tf.shape(conv7)
        feature_seqs = tf.reshape(conv7,shape=[shape[0],shape[1],1024])

In [6]:
show_graph(graph)

## stacked Bidirectional LSTM 구성
---

총 2층의 Bidrectional LSTM Layer가 구성됩니다.

In [7]:
with graph.as_default():
    with tf.variable_scope('recurrent_layers'):
        outputs = feature_seqs
        for i in range(2):
            with tf.variable_scope('bidirectional_{}'.format(i)):
                bidirectional = tf.keras.layers.Bidirectional
                LSTM = tf.keras.layers.LSTM
                outputs = bidirectional(
                    LSTM(256,
                         return_sequences=True))(outputs)
        rnn_seqs = tf.identity(outputs, name='rnn_sequences')

In [8]:
show_graph(graph)

## Transcription Layer 구성
---

학습데이터에 클래스 라벨의 순서만 존재하고, 각 클래스의 위치가 정확히 어디인지 모르는 경우,<br>
CTC(Connectionist Temporal Classification) Loss를 이용합니다.

구체적인 설명은 [Youtube 강좌](https://www.youtube.com/watch?v=GxtMbmv169o)를 들어보면 좋습니다.

In [9]:
with graph.as_default():
    targets = tf.placeholder(tf.int32,shape=(None,None),name='targets')
    with tf.variable_scope('transcription'):
        shape = tf.shape(feature_seqs)
        batch_size, max_len, _ = tf.split(shape, 3, axis=0)
        seq_len = tf.ones(batch_size, tf.int32) * max_len        
        
        # Calculate Loss by CTC
        logits = tf.layers.Dense(num_classes + 1, name='logits')(rnn_seqs)
        logits_tp = tf.transpose(logits,[1,0,2])
        
        indices = tf.where(tf.not_equal(targets, -1))
        values = tf.gather_nd(targets, indices)
        shape = tf.cast(tf.shape(targets),dtype=tf.int64)
        sparse_targets = tf.SparseTensor(indices,values,shape)
        loss = tf.nn.ctc_loss(sparse_targets, logits_tp, seq_len)

        # Calculate the best path by Greedy Algorithm        
        decoded, _ = tf.nn.ctc_greedy_decoder(logits_tp,
                                              sequence_length=seq_len)
        pred = tf.sparse.to_dense(decoded[0]) # Result -> 우리의 예측값
    
    loss = tf.reduce_mean(loss, name='ctc_loss')
    pred = tf.identity(pred, name='prediction')

In [10]:
show_graph(graph)

## Metric 구성
---

두 문자열의 유사도를 측정하는 방식으로는 Levenshtein distance, 별칭 `edit distance`가 있습니다.<br>

값은 0에 가까울수록 두 문자열의 유사도가 완전 일치에 가깝고,1에 가까울수록 완전 불일치에 가깝습니다.

In [11]:
with graph.as_default():
    with tf.variable_scope("metric"):
        label_error_rate = tf.reduce_mean(
            tf.edit_distance(tf.cast(decoded[0], tf.int32),
                             sparse_targets),
            name='label_error_rate')

In [12]:
show_graph(graph)

## Optimizer 구성
---

BatchNormalization을 CNN에 넣었기 때문에, 배치 단위 별 EMA(Mean & Variance)를 위해<br>
update_ops를 호출해야 합니다. 근데 귀찮잖아요. 그래서 아래와 같이 <br>
control_dependencies에 추가해주면, train_op를 부르게 됩니다.

In [13]:
with graph.as_default():
    lr = tf.placeholder_with_default(0.01,None,name='learning_rate')
    update_ops = tf.get_collection(tf.GraphKeys.UPDATE_OPS)
    with tf.control_dependencies(update_ops):
        train_op = (tf.train
                    .AdamOptimizer(learning_rate=lr)
                    .minimize(loss))

In [14]:
show_graph(graph)